In [1]:
import pandas as pd
import dash_leaflet as dl
import dash_leaflet.express as dlx
import os 
import plotly.graph_objects as go
import json
import geopandas as gpd


In [5]:
#mapbox token
token = 'pk.eyJ1IjoiYXVyZmVscyIsImEiOiJja25rZXNka2gwN3owMnNuMHl6MnRzNmUzIn0.tQH40pfi4OG7Q9_vVNtUVg'

#filter for only latest ODK observations
#first read, make date and sort by date
odk = pd.read_csv('updated_data.csv')
odk['today'] = pd.to_datetime(odk['today'])
odk = odk.sort_values('today',ascending=0)
#then drop all duplicates after first record
odk_latest = odk.drop_duplicates('well_no')

#extract lat lon from odk
lat = odk_latest.Geo_location.str.split(expand=True)[0]
lon = odk_latest.Geo_location.str.split(expand=True)[1]

#add back to measurement df with correct format
odk_latest['lat'] = lat.astype('float')
odk_latest['lon'] = lon.astype('float')



#load distric layers to add for context

file = './nepal-distr.geojson'

geo_df = gpd.read_file(file)



<ipython-input-5-f562e7f54912>:17: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  odk_latest['lat'] = lat.astype('float')
<ipython-input-5-f562e7f54912>:18: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  odk_latest['lon'] = lon.astype('float')


In [11]:



mapbox_access_token = token

#fig = px.scatter_geo(odk_latest, color = "gw_level",lat = odk_latest['lat'],
#                     lon = odk_latest['lon'],# size of markers, "pop" is one of the columns of gapminder
#                     ) 





fig = go.Figure([
    go.Scattermapbox(
    mode = "text",
        showlegend = False, 
    lon = [-75, -80, -50], lat = [45, 20, -20],
    marker = {'size': 20, 'symbol': ["bus", "harbor", "airport"]},
    text = ["Bus", "Harbor", "airport"],textposition = "bottom right"),
    
    go.Scattermapbox(
        lat= geo_df.centroid.y,
        lon= geo_df.centroid.x,
        mode='text',
        showlegend = False,
        marker=go.scattermapbox.Marker(
            size=14
        ),
        text= geo_df['DISTRICT'],
    ),    go.Scattermapbox(
    name="GW Level",
    lat=odk_latest['lat'],
    lon=odk_latest['lon'],
    mode='markers',
    marker=go.scattermapbox.Marker(
       size=14,
        color=odk_latest['gw_level'],
        colorscale='RdYlGn_r',
        showscale=True,
        ),
    )
    
    
    

                            
])

fig.update_layout(
    hovermode='closest',
    mapbox=dict(
        accesstoken=token,
        bearing=0,
       center=go.layout.mapbox.Center(
            lat=28.2,
            lon=81.5
        ),
        pitch=0,
        zoom=8,
        layers =  [{
            'source': districts,
            'type': "line", 'below': "traces", 'color': "rgba(147,112,219)",
            "symbol":{"text":"HELLO","placement":"point"}},
]
    )
)

#fig.update_layout(margin={"r":0,"t":0,"l":0,"b":0})

    
fig.show()
